In [1773]:
#Cargamos librerias
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import scipy.special as special
from scipy.optimize import curve_fit
import seaborn as sns
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

In [1774]:
#Cargar archivo csv
df= pd.read_csv("datoslimpioscreta.csv")
df.head()

source      host_location host_response_time  \
0      city scrape  Heraklion, Greece     within an hour   
1      city scrape     Matala, Greece     within an hour   
2  previous scrape     Chania, Greece     within an hour   
3      city scrape             Greece     within an hour   
4      city scrape   Iraklion, Greece     within an hour   

                 host_verifications host_has_profile_pic  \
0                ['email', 'phone']                    t   
1  ['email', 'phone', 'work_email']                    t   
2                ['email', 'phone']                    t   
3                ['email', 'phone']                    t   
4                ['email', 'phone']                    t   

  host_identity_verified                 neighbourhood  \
0                      t                  Gazi, Greece   
1                      t  Matala, Crete Island, Greece   
2                      t                Chania, Greece   
3                      t                  Not provided   
4                      t   Agia Pelagia, Crete, Greece   

  neighbourhood_group_cleansed                      property_type  \
0                 Not provided                 Entire rental unit   
1                 Not provided  Private room in bed and breakfast   
2                 Not provided                 Entire rental unit   
3                 Not provided                 Entire rental unit   
4                 Not provided                 Entire rental unit   

         room_type  ... review_scores_accuracy review_scores_cleanliness  \
0  Entire home/apt  ...                   4.94                      4.91   
1     Private room  ...                   4.14                      4.49   
2  Entire home/apt  ...                   4.71                      4.67   
3  Entire home/apt  ...                   4.50                      5.00   
4  Entire home/apt  ...                   4.87                      4.80   

  review_scores_checkin  review_scores_communication  review_scores_location  \
0                  4.96                         4.99                    4.64   
1                  4.33                         4.43                    4.50   
2                  4.87                         4.84                    4.94   
3                  5.00                         4.50                    4.00   
4                  4.92                         4.94                    4.68   

   review_scores_value  calculated_host_listings_count  \
0                 4.92                               3   
1                 4.18                               4   
2                 4.66                               4   
3                 4.50                               1   
4                 4.88                              13   

   calculated_host_listings_count_entire_homes  \
0                                            3   
1                                            0   
2                                            4   
3                                            1   
4                                           10   

   calculated_host_listings_count_private_rooms  reviews_per_month  
0                                             0               0.82  
1                                             4               0.26  
2                                             0               2.12  
3                                             0               0.01  
4                                             1               0.98  

[5 rows x 54 columns]

In [1775]:
df['price'].mean()

np.float64(226.28497171686286)

In [1776]:
df.select_dtypes(include=['number']).columns

Index(['host_is_superhost', 'host_response_rate', 'host_acceptance_rate',
       'host_listings_count', 'host_total_listings_count', 'latitude',
       'longitude', 'accommodates', 'bathrooms', 'bedrooms', 'beds', 'price',
       'minimum_nights', 'maximum_nights', 'minimum_minimum_nights',
       'maximum_minimum_nights', 'minimum_maximum_nights',
       'maximum_maximum_nights', 'minimum_nights_avg_ntm',
       'maximum_nights_avg_ntm', 'availability_30', 'availability_60',
       'availability_90', 'availability_365', 'number_of_reviews',
       'number_of_reviews_ltm', 'availability_eoy', 'number_of_reviews_ly',
       'estimated_occupancy_l365d', 'estimated_revenue_l365d',
       'review_scores_rating', 'review_scores_accuracy',
       'review_scores_cleanliness', 'review_scores_checkin',
       'review_scores_communication', 'review_scores_location',
       'review_scores_value', 'calculated_host_listings_count',
       'calculated_host_listings_count_entire_homes',
       'calcu

In [1777]:
df.columns[df.isnull().any()]

Index([], dtype='object')

In [1778]:
dicotomicas = [col for col in df.columns if df[col].nunique() == 2]
dicotomicas

['source',
 'host_has_profile_pic',
 'host_identity_verified',
 'instant_bookable',
 'host_is_superhost']

In [1779]:
{col: df[col].unique() for col in dicotomicas}

{'source': array(['city scrape', 'previous scrape'], dtype=object),
 'host_has_profile_pic': array(['t', 'f'], dtype=object),
 'host_identity_verified': array(['t', 'f'], dtype=object),
 'instant_bookable': array(['t', 'f'], dtype=object),
 'host_is_superhost': array([1, 0])}

In [1840]:
import pandas as pd

# --- Columnas numéricas y dicotómicas ---
num_cols = df.select_dtypes(include=['number']).columns
dicotomicas = ['accommodates', 'host_acceptance_rate','reviews_per_month','availability_30','price','source', 'host_has_profile_pic', 'host_identity_verified', 'instant_bookable', 'host_is_superhost']

# --- Lista donde guardaremos los resultados ---
resultados = []

# --- Cálculo de correlaciones ---
for col in dicotomicas:
    df_temp = df.copy()
    # Convertimos la variable dicotómica en numérica temporalmente (0 y 1)
    df_temp[col] = df_temp[col].astype('category').cat.codes
    
    # Calculamos correlaciones absolutas con variables numéricas
    corrs = df_temp[num_cols].corrwith(df_temp[col]).abs().sort_values(ascending=False).head(4)
    
    # Guardamos los resultados en lista
    for variable, corr in corrs.items():
        resultados.append({
            'Variable Dicotómica': col,
            'Variable Numérica': variable,
            'Correlación': round(corr, 3)
        })

# --- Convertimos resultados en DataFrame (tabla) ---
tabla_corr = pd.DataFrame(resultados).sort_values(by='Correlación', ascending=False).reset_index(drop=True)

# --- Mostramos tabla ordenada ---
display(tabla_corr)


Variable Dicotómica                            Variable Numérica  \
0             accommodates                                 accommodates   
1             accommodates                                     bedrooms   
2          availability_30                              availability_60   
3          availability_30                              availability_90   
4             accommodates                                         beds   
5        reviews_per_month                    estimated_occupancy_l365d   
6        reviews_per_month                        number_of_reviews_ltm   
7        reviews_per_month                         number_of_reviews_ly   
8          availability_30                             availability_eoy   
9          availability_30                             availability_365   
10       reviews_per_month                            number_of_reviews   
11                   price                                 accommodates   
12                   price                                     bedrooms   
13                   price                                         beds   
14       host_is_superhost                    estimated_occupancy_l365d   
15                  source                             availability_eoy   
16                  source                             availability_365   
17       host_is_superhost                        number_of_reviews_ltm   
18       host_is_superhost                         number_of_reviews_ly   
19            accommodates  calculated_host_listings_count_entire_homes   
20                  source                              availability_90   
21                   price  calculated_host_listings_count_entire_homes   
22                  source                              availability_60   
23       host_is_superhost               calculated_host_listings_count   
24    host_acceptance_rate                           host_response_rate   
25    host_acceptance_rate                          host_listings_count   
26    host_acceptance_rate                    estimated_occupancy_l365d   
27    host_acceptance_rate                        number_of_reviews_ltm   
28    host_has_profile_pic                       maximum_maximum_nights   
29        instant_bookable                       maximum_maximum_nights   
30    host_has_profile_pic                       maximum_nights_avg_ntm   
31    host_has_profile_pic                               maximum_nights   
32    host_has_profile_pic                       minimum_maximum_nights   
33        instant_bookable                       maximum_nights_avg_ntm   
34        instant_bookable                       minimum_maximum_nights   
35        instant_bookable                           host_response_rate   
36  host_identity_verified                       minimum_maximum_nights   
37  host_identity_verified                    estimated_occupancy_l365d   
38  host_identity_verified                         number_of_reviews_ly   
39  host_identity_verified                        number_of_reviews_ltm   

    Correlación  
0         1.000  
1         0.870  
2         0.832  
3         0.763  
4         0.740  
5         0.672  
6         0.655  
7         0.653  
8         0.627  
9         0.579  
10        0.557  
11        0.530  
12        0.512  
13        0.417  
14        0.381  
15        0.379  
16        0.355  
17        0.349  
18        0.349  
19        0.328  
20        0.309  
21        0.302  
22        0.282  
23        0.274  
24        0.261  
25        0.198  
26        0.155  
27        0.143  
28        0.141  
29        0.134  
30        0.133  
31        0.123  
32        0.120  
33        0.114  
34        0.082  
35        0.078  
36        0.070  
37        0.058  
38        0.052  
39        0.052

**PRIMER CASO**

SOURCE

In [1781]:

#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['availability_eoy', 'availability_365','availability_90']]
Var_Dep= df['source']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

In [1782]:
#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

In [1783]:
#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

LogisticRegression()

In [1784]:
#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

array(['city scrape', 'city scrape', 'city scrape', ..., 'city scrape',
       'city scrape', 'city scrape'], shape=(7850,), dtype=object)

In [1785]:
#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

Matriz de Confusión:
[[7011    0]
 [ 839    0]]


In [1786]:
#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="previous scrape")
print('Precisión del modelo:')
print(precision)

Precisión del modelo:
0.0


c:\Users\sammm\AppData\Local\Programs\Python\Python313\Lib\site-packages\sklearn\metrics\_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])


In [1787]:
#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="city scrape")
print('Precisión del modelo:')
print(precision)

Precisión del modelo:
0.8931210191082802


In [1788]:
#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

Exactitud del modelo:
0.8931210191082802


In [1789]:
#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="city scrape")
print('Sensibilidad del modelo:')
print(sensibilidad)

Sensibilidad del modelo:
1.0


In [1790]:
#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="previous scrape")
print('Sensibilidad del modelo:')
print(sensibilidad)

Sensibilidad del modelo:
0.0


In [1791]:
# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="previous scrape")
print('Puntaje F1 del modelo:')
print(puntajef1)

Puntaje F1 del modelo:
0.0


**SEGUNDO CASO**

MÉTODO 1 PARA **SOURCE** REPONDERACIÓN DE CLASES 

In [1792]:
#Reponderación de las clases
algoritmo_Pond = LogisticRegression(class_weight='balanced')
algoritmo_Pond.fit(X_train, y_train)

LogisticRegression(class_weight='balanced')

In [1793]:
#Realizamos una predicción
y_pred_pond = algoritmo_Pond.predict(X_test) 
y_pred_pond

array(['city scrape', 'previous scrape', 'previous scrape', ...,
       'city scrape', 'city scrape', 'previous scrape'],
      shape=(7850,), dtype=object)

In [1794]:
#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred_pond)
print('Matriz de Confusión:')
print(matriz)

Matriz de Confusión:
[[5283 1728]
 [ 250  589]]


In [1795]:
#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred_pond, average="binary", pos_label="previous scrape")
print('Precisión del modelo:')
print(precision)

Precisión del modelo:
0.2542080276219249


In [1796]:
#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred_pond, average="binary", pos_label="city scrape")
print('Precisión del modelo:')
print(precision)

Precisión del modelo:
0.9548165552141695


In [1797]:
#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred_pond)
print('Exactitud del modelo:')
print(exactitud)

Exactitud del modelo:
0.7480254777070063


In [1798]:
#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred_pond, average="binary", pos_label="previous scrape")
print('Sensibilidad del modelo:')
print(sensibilidad)

Sensibilidad del modelo:
0.7020262216924911


In [1799]:
#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred_pond, average="binary", pos_label="city scrape")
print('Sensibilidad del modelo:')
print(sensibilidad)

Sensibilidad del modelo:
0.7535301668806161


**TERCER CASO**

HOST HAS PROFILE PIC

In [1800]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['maximum_maximum_nights', 'maximum_nights_avg_ntm','maximum_nights']]
Var_Dep= df['host_has_profile_pic']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="t")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="f")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="t")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="f")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="t")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[   0  379]
 [   0 7471]]
Precisión del modelo:
0.9517197452229299
Precisión del modelo:
0.0
Exactitud del modelo:
0.9517197452229299
Sensibilidad del modelo:
1.0
Sensibilidad del modelo:
0.0
Puntaje F1 del modelo:
0.9752627113112721


c:\Users\sammm\AppData\Local\Programs\Python\Python313\Lib\site-packages\sklearn\metrics\_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])


**CUARTO CASO**

MÉTODO 2 PARA **HOST PROFILE PIC** SOBREMUESTREO

In [1801]:
#Aplicamos la técnica de sobremuestreo (oversampling)
from imblearn.over_sampling import SMOTE
smote = SMOTE()
X_resampled, y_resampled = smote.fit_resample(X_train, y_train)

#Entrenamos el modelo sobremuestreado
algoritmo_Over_sampling = LogisticRegression()
algoritmo_Over_sampling.fit(X_resampled, y_resampled)

#Realizamos una predicción
y_pred_over_sampling = algoritmo_Over_sampling.predict(X_test) 
y_pred_over_sampling

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred_over_sampling)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score
precision = precision_score(y_test, y_pred_over_sampling, average="binary", pos_label="t")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score
precision = precision_score(y_test, y_pred_over_sampling, average="binary", pos_label="f")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score
exactitud = accuracy_score(y_test, y_pred_over_sampling)
print('Exactitud del modelo:')
print(exactitud)
#Calculo la sensibilidad del modelo

from sklearn.metrics import recall_score
sensibilidad = recall_score(y_test, y_pred_over_sampling, average="binary", pos_label="t")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo

from sklearn.metrics import recall_score
sensibilidad = recall_score(y_test, y_pred_over_sampling, average="binary", pos_label="f")
print('Sensibilidad del modelo:')
print(sensibilidad)

Matriz de Confusión:
[[ 282   97]
 [2897 4574]]
Precisión del modelo:
0.9792335688289445
Precisión del modelo:
0.0887071406102548
Exactitud del modelo:
0.6185987261146497
Sensibilidad del modelo:
0.6122339713559095
Sensibilidad del modelo:
0.7440633245382586


**QUINTO CASO**

HOST IDENTITY VERIFIED

In [1802]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['price', 'host_is_superhost','minimum_maximum_nights']]
Var_Dep= df['host_identity_verified']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="f")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="f")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="f")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[   0  142]
 [   7 7701]]
Precisión del modelo:
0.0
Exactitud del modelo:
0.9810191082802547
Sensibilidad del modelo:
0.0
Puntaje F1 del modelo:
0.0


**SEXTO CASO**

MÉTODO 1 PARA **HOST IDENTITY VERIFIED** REPONDERACIÓN DE LAS CLASES

In [1803]:
#Reponderación de las clases
algoritmo_Pond = LogisticRegression(class_weight='balanced')
algoritmo_Pond.fit(X_train, y_train)

#Realizamos una predicción
y_pred_pond = algoritmo_Pond.predict(X_test) 
y_pred_pond

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred_pond)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred_pond, average="binary", pos_label="t")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred_pond, average="binary", pos_label="f")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred_pond)
print('Exactitud del modelo:')
print(exactitud)


#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred_pond, average="binary", pos_label="t")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred_pond, average="binary", pos_label="f")
print('Sensibilidad del modelo:')
print(sensibilidad)

Matriz de Confusión:
[[  87   55]
 [2346 5362]]
Precisión del modelo:
0.9898467786597748
Precisión del modelo:
0.035758323057953144
Exactitud del modelo:
0.694140127388535
Sensibilidad del modelo:
0.6956408925791385
Sensibilidad del modelo:
0.6126760563380281


**SÉPTIMO CASO**

INSTANT BOOKABLE

In [1804]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['host_acceptance_rate', 'maximum_maximum_nights','maximum_nights_avg_ntm']]
Var_Dep= df['instant_bookable']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="t")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="f")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="t")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="f")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="f")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[ 774 2082]
 [ 172 4822]]
Precisión del modelo:
0.6984356894553881
Precisión del modelo:
0.8181818181818182
Exactitud del modelo:
0.7128662420382166
Sensibilidad del modelo:
0.9655586704044854
Sensibilidad del modelo:
0.2710084033613445
Puntaje F1 del modelo:
0.407154129405576


**OCTAVO CASO**

In [1805]:
df['host_is_superhost'].unique()

array([1, 0])

In [1806]:
#Conversión de tipo de dato de columna de tipo Object a Float
df['host_is_superhost']= df['host_is_superhost'].astype(str)

HOST IS SUPERHOST

In [1807]:

#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['estimated_occupancy_l365d', 'number_of_reviews_ly','number_of_reviews_ltm']]
Var_Dep= df['host_is_superhost']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="0")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="1")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="0")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="1")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="0")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[4246  460]
 [1789 1355]]
Precisión del modelo:
0.7035625517812759
Precisión del modelo:
0.7465564738292011
Exactitud del modelo:
0.7135031847133758
Sensibilidad del modelo:
0.9022524436889078
Sensibilidad del modelo:
0.4309796437659033
Puntaje F1 del modelo:
0.7906153989386463


**NOVENO CASO**

Creación de Categorias a partir de clases

In [1808]:
#Obtenemos el limite superior y el límite inferior de la columna objetivo
Max=df['price'].max()
Min=df['price'].min()
Limites= [Min, Max]
Limites



[np.int64(12), np.int64(71897)]

In [1809]:
#Categorización de variables
#Declaramos 2 intervalos 
intervalos=[11, 226, 71898]
intervalos

[11, 226, 71898]

In [1810]:
#Creamos las categorías 
categorias= ["Cheap", "Expensive"]

In [1811]:
# Ajustar maximo de filas
pd.options.display.max_rows = None

In [1812]:
#Finalmente creamos las categorías en la columna numérica
df['price']=pd.cut(x= df['price'], bins=intervalos, labels= categorias )

In [1813]:
df['price']

0            Cheap
1            Cheap
2            Cheap
3            Cheap
4            Cheap
5            Cheap
6            Cheap
7            Cheap
8            Cheap
9            Cheap
10           Cheap
11           Cheap
12           Cheap
13           Cheap
14           Cheap
15           Cheap
16           Cheap
17           Cheap
18           Cheap
19           Cheap
20           Cheap
21           Cheap
22           Cheap
23           Cheap
24           Cheap
25           Cheap
26           Cheap
27           Cheap
28           Cheap
29           Cheap
30           Cheap
31           Cheap
32           Cheap
33           Cheap
34           Cheap
35           Cheap
36           Cheap
37           Cheap
38           Cheap
39           Cheap
40           Cheap
41           Cheap
42           Cheap
43           Cheap
44           Cheap
45           Cheap
46       Expensive
47           Cheap
48           Cheap
49           Cheap
50           Cheap
51       Expensive
52          

In [1814]:
df['price'].unique()

['Cheap', 'Expensive']
Categories (2, object): ['Cheap' < 'Expensive']

In [1815]:
#Analizar categorias de una columna
df6 = df.groupby(['price'])['price'].count()
df6

C:\Users\sammm\AppData\Local\Temp\ipykernel_21516\2017339439.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df6 = df.groupby(['price'])['price'].count()


price
Cheap        21460
Expensive     4704
Name: price, dtype: int64

In [1816]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['accommodates', 'beds','bedrooms']]
Var_Dep= df['price']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Cheap")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Expensive")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Cheap")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Expensive")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="Cheap")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[6236  242]
 [ 834  538]]
Precisión del modelo:
0.882036775106082
Precisión del modelo:
0.6897435897435897
Exactitud del modelo:
0.8629299363057324
Sensibilidad del modelo:
0.9626427909848718
Sensibilidad del modelo:
0.39212827988338195
Puntaje F1 del modelo:
0.9205786832004724


**DÉCIMO CASO**

Creación de categorías a partir de clases

In [1817]:
#Obtenemos el limite superior y el límite inferior de la columna objetivo
Max=df['availability_30'].max()
Min=df['availability_30'].min()
Limites= [Min, Max]
Limites

[np.int64(0), np.int64(30)]

In [1818]:
#Categorización de variables
#Declaramos 2 intervalos 
intervalos=np.linspace(-1, 31, 3)
intervalos

array([-1., 15., 31.])

In [1819]:
#Creamos las categorías 
categorias= ["Ocupación primera mitad del mes", "Ocupación segunda mitad del mes"]

In [1820]:
# Ajustar maximo de filas
pd.options.display.max_rows = None

In [1821]:
#Finalmente creamos las categorías en la columna numérica
df['availability_30']=pd.cut(x= df['availability_30'], bins=intervalos, labels= categorias )

In [1822]:
df['availability_30']

0        Ocupación segunda mitad del mes
1        Ocupación primera mitad del mes
2        Ocupación segunda mitad del mes
3        Ocupación segunda mitad del mes
4        Ocupación primera mitad del mes
5        Ocupación segunda mitad del mes
6        Ocupación primera mitad del mes
7        Ocupación segunda mitad del mes
8        Ocupación segunda mitad del mes
9        Ocupación segunda mitad del mes
10       Ocupación primera mitad del mes
11       Ocupación segunda mitad del mes
12       Ocupación primera mitad del mes
13       Ocupación segunda mitad del mes
14       Ocupación segunda mitad del mes
15       Ocupación primera mitad del mes
16       Ocupación primera mitad del mes
17       Ocupación segunda mitad del mes
18       Ocupación primera mitad del mes
19       Ocupación segunda mitad del mes
20       Ocupación segunda mitad del mes
21       Ocupación primera mitad del mes
22       Ocupación primera mitad del mes
23       Ocupación segunda mitad del mes
24       Ocupaci

AVAILABILITY 30

In [1823]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['availability_eoy', 'availability_60','availability_90']]
Var_Dep= df['availability_30']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Ocupación primera mitad del mes")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Ocupación segunda mitad del mes")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Ocupación primera mitad del mes")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Ocupación segunda mitad del mes")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="Ocupación primera mitad del mes")
print('Puntaje F1 del modelo:')
print(puntajef1)

Matriz de Confusión:
[[3711  348]
 [ 340 3451]]
Precisión del modelo:
0.9160701061466304
Precisión del modelo:
0.9083969465648855
Exactitud del modelo:
0.9123566878980892
Sensibilidad del modelo:
0.9142645971914265
Sensibilidad del modelo:
0.9103139013452914
Puntaje F1 del modelo:
0.9151664611590629


**DÉCIMO PRIMER CASO**

Creación de categorías a partir de clases

In [1824]:
#Obtenemos el limite superior y el límite inferior de la columna objetivo
Max=df['reviews_per_month'].max()
Min=df['reviews_per_month'].min()
Limites= [Min, Max]
Limites



[np.float64(0.01), np.float64(9.57)]

In [1825]:
#Categorización de variables
#Declaramos 2 intervalos 
intervalos=(0.00, 0.47, 9.58)
intervalos

(0.0, 0.47, 9.58)

In [1826]:
#Creamos las categorías 
categorias= ["Menos de 5", "Más de 5"]

In [1827]:
# Ajustar maximo de filas
pd.options.display.max_rows = None

In [1828]:
#Finalmente creamos las categorías en la columna numérica
df['reviews_per_month']=pd.cut(x= df['reviews_per_month'], bins=intervalos, labels= categorias )

In [1829]:
df['reviews_per_month']

0          Más de 5
1        Menos de 5
2          Más de 5
3        Menos de 5
4          Más de 5
5        Menos de 5
6        Menos de 5
7        Menos de 5
8        Menos de 5
9        Menos de 5
10         Más de 5
11         Más de 5
12         Más de 5
13       Menos de 5
14         Más de 5
15         Más de 5
16         Más de 5
17       Menos de 5
18       Menos de 5
19         Más de 5
20       Menos de 5
21       Menos de 5
22       Menos de 5
23       Menos de 5
24       Menos de 5
25         Más de 5
26       Menos de 5
27       Menos de 5
28       Menos de 5
29         Más de 5
30         Más de 5
31       Menos de 5
32       Menos de 5
33       Menos de 5
34       Menos de 5
35       Menos de 5
36       Menos de 5
37         Más de 5
38       Menos de 5
39       Menos de 5
40       Menos de 5
41       Menos de 5
42         Más de 5
43       Menos de 5
44         Más de 5
45         Más de 5
46       Menos de 5
47       Menos de 5
48       Menos de 5
49       Menos de 5


In [1830]:
#Analizar categorias de una columna
df6 = df.groupby(['reviews_per_month'])['reviews_per_month'].count()
df6

C:\Users\sammm\AppData\Local\Temp\ipykernel_21516\2166217304.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df6 = df.groupby(['reviews_per_month'])['reviews_per_month'].count()


reviews_per_month
Menos de 5    18490
Más de 5       7674
Name: reviews_per_month, dtype: int64

REVIEWS PER MONTH

In [1831]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['number_of_reviews_ltm', 'number_of_reviews_ly','estimated_occupancy_l365d']]
Var_Dep= df['reviews_per_month']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score
precision = precision_score(y_test, y_pred, average="binary", pos_label="Más de 5")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Menos de 5")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Más de 5")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Menos de 5")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="Más de 5")
print('Puntaje F1 del modelo:')
print(puntajef1)


Matriz de Confusión:
[[5231  299]
 [ 489 1831]]
Precisión del modelo:
0.85962441314554
Precisión del modelo:
0.9145104895104895
Exactitud del modelo:
0.8996178343949045
Sensibilidad del modelo:
0.7892241379310345
Sensibilidad del modelo:
0.9459312839059675
Puntaje F1 del modelo:
0.8229213483146067


**DÉCIMO SEGUNDO MODELO**

Creación de Categorias a partir de clases

In [1832]:
#Obtenemos el limite superior y el límite inferior de la columna objetivo
Max=df['host_acceptance_rate'].max()
Min=df['host_acceptance_rate'].min()
Limites= [Min, Max]
Limites

[np.float64(0.0), np.float64(1.0)]

In [1833]:
#Categorización de variables
#Declaramos 2 intervalos 
intervalos=np.linspace(-1, 2, 3)
intervalos

array([-1. ,  0.5,  2. ])

In [1834]:
#Creamos las categorías 
categorias= ["Menos de la mitad", "Más de la mitad"]

In [1835]:
# Ajustar maximo de filas
pd.options.display.max_rows = None

In [1836]:
#Finalmente creamos las categorías en la columna numérica
df['host_acceptance_rate']=pd.cut(x= df['host_acceptance_rate'], bins=intervalos, labels= categorias )

In [1837]:
df['host_acceptance_rate']

0          Más de la mitad
1          Más de la mitad
2          Más de la mitad
3        Menos de la mitad
4          Más de la mitad
5          Más de la mitad
6          Más de la mitad
7          Más de la mitad
8          Más de la mitad
9        Menos de la mitad
10         Más de la mitad
11         Más de la mitad
12         Más de la mitad
13         Más de la mitad
14         Más de la mitad
15         Más de la mitad
16         Más de la mitad
17         Más de la mitad
18         Más de la mitad
19         Más de la mitad
20         Más de la mitad
21         Más de la mitad
22       Menos de la mitad
23         Más de la mitad
24         Más de la mitad
25         Más de la mitad
26         Más de la mitad
27       Menos de la mitad
28         Más de la mitad
29         Más de la mitad
30         Más de la mitad
31         Más de la mitad
32         Más de la mitad
33         Más de la mitad
34         Más de la mitad
35         Más de la mitad
36         Más de la mitad
3

In [1838]:
#Analizar categorias de una columna
df6 = df.groupby(['host_acceptance_rate'])['host_acceptance_rate'].count()
df6

C:\Users\sammm\AppData\Local\Temp\ipykernel_21516\2448230977.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df6 = df.groupby(['host_acceptance_rate'])['host_acceptance_rate'].count()


host_acceptance_rate
Menos de la mitad     1624
Más de la mitad      24540
Name: host_acceptance_rate, dtype: int64

In [ ]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['estimated_occupancy_l365d', 'host_response_rate','calculated_host_listings_count_private_rooms']]
Var_Dep= df['host_acceptance_rate']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score
precision = precision_score(y_test, y_pred, average="binary", pos_label="Más de la mitad")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Menos de la mitad")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Más de la mitad")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Menos de la mitad")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="Más de la mitad")
print('Puntaje F1 del modelo:')
print(puntajef1)


Matriz de Confusión:
[[  37  443]
 [  41 7329]]
Precisión del modelo:
0.9430005146680391
Precisión del modelo:
0.47435897435897434
Exactitud del modelo:
0.938343949044586
Sensibilidad del modelo:
0.9944369063772048
Sensibilidad del modelo:
0.07708333333333334
Puntaje F1 del modelo:
0.9680359265618809


**DÉCIMO TERCER CASO**

Creación de Categorias a partir de clases

In [1841]:
#Obtenemos el limite superior y el límite inferior de la columna objetivo
Max=df['accommodates'].max()
Min=df['accommodates'].min()
Limites= [Min, Max]
Limites

[np.int64(1), np.int64(16)]

In [1842]:
#Categorización de variables
#Declaramos 2 intervalos 
intervalos=np.linspace(0, 17, 3)
intervalos

array([ 0. ,  8.5, 17. ])

In [1843]:
#Creamos las categorías 
categorias= ["Pocos huespedes", "Muchos huespedes"]

In [1844]:
# Ajustar maximo de filas
pd.options.display.max_rows = None

In [1845]:
#Finalmente creamos las categorías en la columna numérica
df['accommodates']=pd.cut(x= df['accommodates'], bins=intervalos, labels= categorias )

In [1847]:
df['accommodates']

0         Pocos huespedes
1         Pocos huespedes
2         Pocos huespedes
3         Pocos huespedes
4         Pocos huespedes
5         Pocos huespedes
6         Pocos huespedes
7         Pocos huespedes
8         Pocos huespedes
9         Pocos huespedes
10        Pocos huespedes
11        Pocos huespedes
12        Pocos huespedes
13        Pocos huespedes
14        Pocos huespedes
15        Pocos huespedes
16        Pocos huespedes
17        Pocos huespedes
18        Pocos huespedes
19        Pocos huespedes
20        Pocos huespedes
21        Pocos huespedes
22        Pocos huespedes
23        Pocos huespedes
24        Pocos huespedes
25        Pocos huespedes
26        Pocos huespedes
27        Pocos huespedes
28        Pocos huespedes
29        Pocos huespedes
30        Pocos huespedes
31        Pocos huespedes
32        Pocos huespedes
33        Pocos huespedes
34        Pocos huespedes
35        Pocos huespedes
36        Pocos huespedes
37        Pocos huespedes
38        Po

ACCOMMODATES

In [1848]:
#Declaramos las variables dependientes e independientes para la regresión Logística
Vars_Indep= df[['calculated_host_listings_count_entire_homes', 'bedrooms','beds']]
Var_Dep= df['accommodates']
#Redefinimos las variables 
X= Vars_Indep
y= Var_Dep
#Dividimos el conjunto de datos en la parte de entrenamiento y prueba:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state =None)
#Se escalan todos los datos
escalar = StandardScaler()
#Para realizar el escalamiento de las variables “X” tanto de entrenamiento como de prueba, utilizaremos fit_transform
X_train = escalar.fit_transform(X_train)
X_test = escalar.transform(X_test)

#Definimos el algoritmo a utilizar
from sklearn.linear_model import LogisticRegression
algoritmo = LogisticRegression()

#Entrenamos el modelo
algoritmo.fit(X_train, y_train)

#Realizamos una predicción
y_pred = algoritmo.predict(X_test) 
y_pred

#Verifico la matriz de Confusión
from sklearn.metrics import confusion_matrix
matriz = confusion_matrix(y_test, y_pred)
print('Matriz de Confusión:')
print(matriz)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score
precision = precision_score(y_test, y_pred, average="binary", pos_label="Pocos huespedes")
print('Precisión del modelo:')
print(precision)

#Calculo la precisión del modelo
from sklearn.metrics import precision_score

precision = precision_score(y_test, y_pred, average="binary", pos_label="Muchos huespedes")
print('Precisión del modelo:')
print(precision)

#Calculo la exactitud del modelo
from sklearn.metrics import accuracy_score

exactitud = accuracy_score(y_test, y_pred)
print('Exactitud del modelo:')
print(exactitud)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Pocos huespedes")
print('Sensibilidad del modelo:')
print(sensibilidad)

#Calculo la sensibilidad del modelo
from sklearn.metrics import recall_score

sensibilidad = recall_score(y_test, y_pred, average="binary", pos_label="Muchos huespedes")
print('Sensibilidad del modelo:')
print(sensibilidad)

# el puntaje F1 que es una combinación entre la precisión y la sensibilidad, para esto importamos f1_score.
#Calculo el Puntaje F1 del modelo
from sklearn.metrics import f1_score

puntajef1 = f1_score(y_test, y_pred, average="binary", pos_label="Pocos huespedes")
print('Puntaje F1 del modelo:')
print(puntajef1)


Matriz de Confusión:
[[ 421  185]
 [  65 7179]]
Precisión del modelo:
0.974877783813145
Precisión del modelo:
0.8662551440329218
Exactitud del modelo:
0.9681528662420382
Sensibilidad del modelo:
0.9910270568746549
Sensibilidad del modelo:
0.6947194719471947
Puntaje F1 del modelo:
0.9828860898138007
